# 73. ITQ-LSH Accuracy Evaluation on ANN Benchmarks

## Purpose
- Train ITQ-LSH (128-bit) on each of 5 ANN benchmark datasets
- Evaluate hash quality: Hamming-Cosine Spearman correlation
- Evaluate Pipeline C-only: ITQ -> Hamming top-K -> Cosine rerank
- Report Recall@1, @10, @100 at various candidate limits

## 0. Setup

In [1]:
import numpy as np
import time
import sys
from pathlib import Path
from tqdm import tqdm
from scipy.stats import spearmanr

sys.path.insert(0, '../src')
from itq_lsh import ITQLSH, hamming_distance_batch

DATA_DIR = Path('../data')
np.random.seed(42)

DATASET_KEYS = ['glove', 'sift', 'fashion', 'nytimes', 'gist']
N_BITS_MAX = 128
ITQ_TRAIN_SUBSAMPLE = 100_000
CANDIDATE_LIMITS = [100, 500, 1000, 2000, 5000]
TOP_K_VALUES = [1, 10, 100]

# Popcount lookup table for uint8
POPCOUNT_TABLE = np.array([bin(i).count('1') for i in range(256)], dtype=np.int32)

def pack_bits(binary_hashes):
    """Pack (N, n_bits) uint8 binary -> (N, ceil(n_bits/8)) uint8 packed."""
    n, n_bits = binary_hashes.shape
    n_bytes = (n_bits + 7) // 8
    # Pad to multiple of 8
    if n_bits % 8 != 0:
        padding = np.zeros((n, 8 - n_bits % 8), dtype=np.uint8)
        binary_hashes = np.hstack([binary_hashes, padding])
    return np.packbits(binary_hashes, axis=1)

def hamming_batch_packed(query_packed, db_packed):
    """Fast Hamming distance using XOR + popcount on packed bytes."""
    xor = np.bitwise_xor(query_packed, db_packed)  # (N, n_bytes)
    return POPCOUNT_TABLE[xor].sum(axis=1)  # (N,)

print(f'Configuration:')
print(f'  N_BITS_MAX={N_BITS_MAX}, ITQ_TRAIN_SUBSAMPLE={ITQ_TRAIN_SUBSAMPLE:,}')
print(f'  CANDIDATE_LIMITS={CANDIDATE_LIMITS}')
print(f'  TOP_K_VALUES={TOP_K_VALUES}')
print(f'  Using bit-packed Hamming distance for speed')

Configuration:
  N_BITS_MAX=128, ITQ_TRAIN_SUBSAMPLE=100,000
  CANDIDATE_LIMITS=[100, 500, 1000, 2000, 5000]
  TOP_K_VALUES=[1, 10, 100]
  Using bit-packed Hamming distance for speed


## 1. Load Data

In [2]:
datasets = {}
for key in DATASET_KEYS:
    prefix = f'ann_{key}'
    train_path = DATA_DIR / f'{prefix}_train.npy'
    if not train_path.exists():
        print(f'{key}: SKIPPED (data not found)')
        continue
    
    datasets[key] = {
        'train': np.load(DATA_DIR / f'{prefix}_train.npy'),
        'test': np.load(DATA_DIR / f'{prefix}_test.npy'),
        'gt': np.load(DATA_DIR / f'{prefix}_gt_neighbors.npy'),
    }
    d = datasets[key]
    print(f'{key}: train={d["train"].shape}, test={d["test"].shape}, gt={d["gt"].shape}')

print(f'\nLoaded {len(datasets)} datasets')

glove: train=(1183514, 100), test=(10000, 100), gt=(10000, 100)


sift: train=(1000000, 128), test=(10000, 128), gt=(10000, 100)
fashion: train=(60000, 784), test=(10000, 784), gt=(10000, 100)


nytimes: train=(290000, 256), test=(10000, 256), gt=(10000, 100)


gist: train=(1000000, 960), test=(1000, 960), gt=(1000, 100)

Loaded 5 datasets


## 2. Train ITQ-LSH for Each Dataset

In [3]:
def train_itq_for_dataset(train_data, n_bits=128, subsample=100_000, seed=42):
    """Train ITQ-LSH, subsampling if dataset is large."""
    n_samples = len(train_data)
    dim = train_data.shape[1]
    
    # ITQ can't produce more bits than input dimensions
    actual_bits = min(n_bits, dim)
    if actual_bits < n_bits:
        print(f'  NOTE: dim={dim} < n_bits={n_bits}, using {actual_bits} bits')
    
    if n_samples > subsample:
        rng = np.random.default_rng(seed)
        indices = rng.choice(n_samples, subsample, replace=False)
        fit_data = train_data[indices]
        print(f'  Subsampled {subsample:,} from {n_samples:,}')
    else:
        fit_data = train_data
        print(f'  Using all {n_samples:,} samples')
    
    itq = ITQLSH(n_bits=actual_bits, n_iterations=50, seed=seed)
    start = time.time()
    itq.fit(fit_data)
    train_time = time.time() - start
    
    return itq, train_time, actual_bits

itq_models = {}
dataset_bits = {}  # Track actual bits per dataset

for key in datasets:
    dim = datasets[key]['train'].shape[1]
    print(f'\n{"="*60}')
    print(f'Training ITQ-LSH for {key} (dim={dim})')
    
    itq, train_time, actual_bits = train_itq_for_dataset(
        datasets[key]['train'], n_bits=N_BITS_MAX, subsample=ITQ_TRAIN_SUBSAMPLE
    )
    itq_models[key] = itq
    dataset_bits[key] = actual_bits
    itq.save(str(DATA_DIR / f'ann_{key}_itq_{actual_bits}bits.pkl'))
    print(f'  Bits: {actual_bits}, Training time: {train_time:.1f}s')

print(f'\nDataset bits: {dataset_bits}')


Training ITQ-LSH for glove (dim=100)
  NOTE: dim=100 < n_bits=128, using 100 bits
  Subsampled 100,000 from 1,183,514
ITQ学習開始: samples=100000, dim=100, bits=100
  Centering完了: mean_norm=1.9604
  PCA完了: explained_variance=100.00%


  ITQ iteration 10: quantization_error=0.4414


  ITQ iteration 20: quantization_error=0.4394


  ITQ iteration 30: quantization_error=0.4382


  ITQ iteration 40: quantization_error=0.4375


...

  ITQ iteration 10: quantization_error=0.9376


  ITQ iteration 20: quantization_error=0.9374


  ITQ iteration 30: quantization_error=0.9373


  ITQ iteration 40: quantization_error=0.9372


  ITQ iteration 50: quantization_error=0.9372
ITQ学習完了
  Bits: 128, Training time: 12.3s

Dataset bits: {'glove': 100, 'sift': 128, 'fashion': 128, 'nytimes': 128, 'gist': 128}


## 3. Transform to Hashes

In [4]:
def transform_in_batches(itq, data, batch_size=50000):
    """Transform large arrays in batches."""
    n = len(data)
    all_hashes = []
    for start in range(0, n, batch_size):
        end = min(start + batch_size, n)
        hashes = itq.transform(data[start:end])
        all_hashes.append(hashes)
    return np.vstack(all_hashes)

hash_data = {}
packed_data = {}  # Bit-packed versions for fast Hamming

for key in datasets:
    n_bits = dataset_bits[key]
    print(f'\n{key}: Transforming to {n_bits}-bit hashes...')
    start = time.time()
    
    train_hashes = transform_in_batches(itq_models[key], datasets[key]['train'])
    test_hashes = transform_in_batches(itq_models[key], datasets[key]['test'])
    
    hash_data[key] = {'train': train_hashes, 'test': test_hashes}
    
    # Create packed versions
    train_packed = pack_bits(train_hashes)
    test_packed = pack_bits(test_hashes)
    packed_data[key] = {'train': train_packed, 'test': test_packed}
    
    elapsed = time.time() - start
    
    # Bit balance check
    balance = train_hashes.mean()
    print(f'  train={train_hashes.shape}, test={test_hashes.shape}')
    print(f'  packed: train={train_packed.shape}, test={test_packed.shape}')
    print(f'  Bit balance: {balance:.3f}, Time: {elapsed:.1f}s')
    
    # Verify packed matches unpacked
    verify_n = min(100, len(test_hashes))
    for i in range(verify_n):
        d1 = hamming_distance_batch(test_hashes[i], train_hashes[:1000])
        d2 = hamming_batch_packed(test_packed[i], train_packed[:1000])
        assert np.allclose(d1, d2), f'Packed verification failed at {key} query {i}'
    print(f'  Packed verification passed ({verify_n} queries)')
    
    # Save
    np.save(DATA_DIR / f'ann_{key}_train_hashes_{n_bits}bits.npy', train_hashes)
    np.save(DATA_DIR / f'ann_{key}_test_hashes_{n_bits}bits.npy', test_hashes)


glove: Transforming to 100-bit hashes...


  train=(1183514, 100), test=(10000, 100)
  packed: train=(1183514, 13), test=(10000, 13)
  Bit balance: 0.501, Time: 0.5s
  Packed verification passed (100 queries)

sift: Transforming to 128-bit hashes...


  train=(1000000, 128), test=(10000, 128)
  packed: train=(1000000, 16), test=(10000, 16)
  Bit balance: 0.502, Time: 0.5s
  Packed verification passed (100 queries)

fashion: Transforming to 128-bit hashes...


  train=(60000, 128), test=(10000, 128)
  packed: train=(60000, 16), test=(10000, 16)
  Bit balance: 0.500, Time: 0.1s
  Packed verification passed (100 queries)

nytimes: Transforming to 128-bit hashes...


  train=(290000, 128), test=(10000, 128)
  packed: train=(290000, 16), test=(10000, 16)
  Bit balance: 0.500, Time: 0.2s
  Packed verification passed (100 queries)

gist: Transforming to 128-bit hashes...


  train=(1000000, 128), test=(1000, 128)
  packed: train=(1000000, 16), test=(1000, 16)
  Bit balance: 0.499, Time: 2.9s
  Packed verification passed (100 queries)


## 4. Hash Quality: Hamming-Cosine Spearman Correlation

In [5]:
def evaluate_hash_quality(train_emb, train_packed, n_queries=200, n_docs=5000, seed=42):
    """Hamming-Cosine Spearman correlation using packed Hamming."""
    rng = np.random.default_rng(seed)
    n = len(train_emb)
    
    qi = rng.choice(n, min(n_queries, n), replace=False)
    di = rng.choice(n, min(n_docs, n), replace=False)
    
    doc_embs = train_emb[di]
    doc_norms = np.linalg.norm(doc_embs, axis=1)
    doc_norms[doc_norms == 0] = 1.0
    doc_packed = train_packed[di]
    
    all_hamming = []
    all_cosine = []
    
    for q_idx in qi:
        q_emb = train_emb[q_idx]
        q_norm = np.linalg.norm(q_emb)
        if q_norm == 0:
            continue
        cos_sims = (doc_embs @ q_emb) / (doc_norms * q_norm)
        h_dists = hamming_batch_packed(train_packed[q_idx], doc_packed)
        all_cosine.extend(cos_sims)
        all_hamming.extend(h_dists)
    
    corr, pval = spearmanr(all_hamming, all_cosine)
    return corr, pval

print('='*80)
print('Hash Quality: Hamming-Cosine Spearman Correlation')
print('='*80)

quality_results = {}
for key in datasets:
    corr, pval = evaluate_hash_quality(
        datasets[key]['train'], packed_data[key]['train']
    )
    quality_results[key] = corr
    dim = datasets[key]['train'].shape[1]
    bits = dataset_bits[key]
    print(f'  {key:>10} (D={dim:>4}, B={bits:>3}): Spearman={corr:.4f} (p={pval:.2e})')

Hash Quality: Hamming-Cosine Spearman Correlation


       glove (D= 100, B=100): Spearman=-0.5083 (p=0.00e+00)


        sift (D= 128, B=128): Spearman=-0.9252 (p=0.00e+00)


     fashion (D= 784, B=128): Spearman=-0.7446 (p=0.00e+00)


     nytimes (D= 256, B=128): Spearman=-0.5084 (p=0.00e+00)


        gist (D= 960, B=128): Spearman=-0.4551 (p=0.00e+00)


## 5. C-only Pipeline Evaluation

In [6]:
def evaluate_c_only(test_embs, test_packed, train_embs, train_packed,
                    gt_neighbors, candidate_limits, top_k_values=[1, 10, 100]):
    """Pipeline C-only: ITQ -> Hamming top-K -> Cosine rerank.
    
    Uses bit-packed Hamming distance. Computes distances once per query.
    """
    n_queries = len(test_embs)
    n_train = len(train_embs)
    max_limit = max(candidate_limits)
    
    train_norms = np.linalg.norm(train_embs, axis=1)
    train_norms[train_norms == 0] = 1.0
    
    recalls = {limit: {k: [] for k in top_k_values} for limit in candidate_limits}
    
    for qi in tqdm(range(n_queries), desc='C-only eval'):
        q_packed = test_packed[qi]
        q_emb = test_embs[qi]
        q_norm = np.linalg.norm(q_emb)
        if q_norm == 0:
            q_norm = 1.0
        
        # Compute Hamming distances ONCE (packed)
        h_dists = hamming_batch_packed(q_packed, train_packed)
        
        # Get top max_limit candidates
        if max_limit < n_train:
            max_cand_idx = np.argpartition(h_dists, max_limit)[:max_limit]
            sorted_order = np.argsort(h_dists[max_cand_idx])
            max_cand_sorted = max_cand_idx[sorted_order]
        else:
            max_cand_sorted = np.argsort(h_dists)
        
        for cand_limit in candidate_limits:
            cand_idx = max_cand_sorted[:cand_limit]
            
            cos_sims = (train_embs[cand_idx] @ q_emb) / (train_norms[cand_idx] * q_norm)
            reranked = cand_idx[np.argsort(-cos_sims)]
            
            for k in top_k_values:
                gt_set = set(gt_neighbors[qi, :k])
                pred_set = set(reranked[:k])
                recalls[cand_limit][k].append(len(gt_set & pred_set) / k)
    
    results = {}
    for cand_limit in candidate_limits:
        results[cand_limit] = {k: np.mean(recalls[cand_limit][k]) for k in top_k_values}
    
    return results

print('='*80)
print('C-only Pipeline: ITQ -> Hamming top-K -> Cosine rerank')
print('='*80)

C-only Pipeline: ITQ -> Hamming top-K -> Cosine rerank


In [7]:
c_only_results = {}

for key in datasets:
    print(f'\n{"="*60}')
    print(f'{key} (N={len(datasets[key]["train"]):,}, D={datasets[key]["train"].shape[1]}, B={dataset_bits[key]})')
    
    start = time.time()
    results = evaluate_c_only(
        datasets[key]['test'], packed_data[key]['test'],
        datasets[key]['train'], packed_data[key]['train'],
        datasets[key]['gt'],
        candidate_limits=CANDIDATE_LIMITS,
        top_k_values=TOP_K_VALUES
    )
    elapsed = time.time() - start
    c_only_results[key] = results
    
    print(f'\n  Results ({elapsed:.0f}s):')
    print(f'  {"Limit":>8} {"R@1":>8} {"R@10":>8} {"R@100":>8}')
    print(f'  {"-"*36}')
    for limit in CANDIDATE_LIMITS:
        r = results[limit]
        print(f'  {limit:>8} {r[1]*100:>7.1f}% {r[10]*100:>7.1f}% {r[100]*100:>7.1f}%')


glove (N=1,183,514, D=100, B=100)


C-only eval:   0%|          | 0/10000 [00:00<?, ?it/s]

C-only eval:   0%|          | 2/10000 [00:00<15:58, 10.43it/s]

C-only eval:   0%|          | 4/10000 [00:00<16:04, 10.36it/s]

C-only eval:   0%|          | 6/10000 [00:00<16:08, 10.32it/s]

...

C-only eval: 100%|█████████▉| 995/1000 [01:38<00:00, 10.05it/s]

C-only eval: 100%|█████████▉| 997/1000 [01:38<00:00, 10.08it/s]

C-only eval: 100%|█████████▉| 999/1000 [01:38<00:00, 10.07it/s]

C-only eval: 100%|██████████| 1000/1000 [01:38<00:00, 10.14it/s]


  Results (101s):
     Limit      R@1     R@10    R@100
  ------------------------------------
       100    41.1%    26.5%    12.3%
       500    64.1%    48.1%    29.7%
      1000    72.9%    59.4%    40.3%
      2000    80.0%    70.2%    52.2%
      5000    89.3%    83.0%    68.7%


## 6. Filter Recall Analysis

In [8]:
def compute_filter_recall(test_packed, train_packed, gt_neighbors,
                          candidate_limits, top_k=10):
    """Fraction of true top-K in Hamming candidates (packed)."""
    n_queries = len(test_packed)
    max_limit = max(candidate_limits)
    results = {limit: [] for limit in candidate_limits}
    
    for qi in tqdm(range(n_queries), desc='Filter Recall'):
        h_dists = hamming_batch_packed(test_packed[qi], train_packed)
        gt_set = set(gt_neighbors[qi, :top_k])
        
        if max_limit < len(train_packed):
            max_cand = np.argpartition(h_dists, max_limit)[:max_limit]
            sorted_order = np.argsort(h_dists[max_cand])
            max_cand_sorted = max_cand[sorted_order]
        else:
            max_cand_sorted = np.argsort(h_dists)
        
        for limit in candidate_limits:
            cand = set(max_cand_sorted[:limit])
            results[limit].append(len(gt_set & cand) / top_k)
    
    return {limit: np.mean(results[limit]) for limit in candidate_limits}

print('='*80)
print('Filter Recall (true top-10 in Hamming candidates)')
print('='*80)

filter_recalls = {}
for key in datasets:
    fr = compute_filter_recall(
        packed_data[key]['test'], packed_data[key]['train'],
        datasets[key]['gt'], CANDIDATE_LIMITS
    )
    filter_recalls[key] = fr
    print(f'  {key:>10}: ', end='')
    for limit in CANDIDATE_LIMITS:
        print(f'L={limit}: {fr[limit]*100:.1f}%  ', end='')
    print()

Filter Recall (true top-10 in Hamming candidates)


Filter Recall:   0%|          | 0/10000 [00:00<?, ?it/s]

Filter Recall:   0%|          | 1/10000 [00:00<19:16,  8.65it/s]

Filter Recall:   0%|          | 2/10000 [00:00<17:47,  9.36it/s]

Filter Recall:   0%|          | 4/10000 [00:00<16:14, 10.26it/s]

...

Filter Recall: 100%|█████████▉| 996/1000 [01:18<00:00, 12.82it/s]

Filter Recall: 100%|█████████▉| 998/1000 [01:18<00:00, 12.81it/s]

Filter Recall: 100%|██████████| 1000/1000 [01:18<00:00, 12.78it/s]

Filter Recall: 100%|██████████| 1000/1000 [01:18<00:00, 12.72it/s]

        gist: L=100: 26.5%  L=500: 48.1%  L=1000: 59.5%  L=2000: 70.2%  L=5000: 83.0%  


## 7. Summary

In [9]:
print('='*80)
print('ITQ-LSH Accuracy Summary (Recall@10)')
print('='*80)

print(f'\n{"Dataset":<12} {"Dim":>5} {"Bits":>5} {"N_train":>10}', end='')
for limit in CANDIDATE_LIMITS:
    print(f' {"L="+str(limit):>8}', end='')
print(f' {"Spearman":>10}')
print('-'*90)

for key in datasets:
    dim = datasets[key]['train'].shape[1]
    n = len(datasets[key]['train'])
    bits = dataset_bits[key]
    print(f'{key:<12} {dim:>5} {bits:>5} {n:>10,}', end='')
    for limit in CANDIDATE_LIMITS:
        r10 = c_only_results[key][limit][10]
        print(f' {r10*100:>7.1f}%', end='')
    print(f' {quality_results[key]:>9.4f}')

print(f'\n{"Dataset":<12} {"Dim":>5}', end='')
for limit in CANDIDATE_LIMITS:
    print(f' {"L="+str(limit):>8}', end='')
print('  (Filter Recall@10)')
print('-'*75)
for key in datasets:
    dim = datasets[key]['train'].shape[1]
    print(f'{key:<12} {dim:>5}', end='')
    for limit in CANDIDATE_LIMITS:
        fr = filter_recalls[key][limit]
        print(f' {fr*100:>7.1f}%', end='')
    print()

# Save results for notebook 74-75
np.save(DATA_DIR / 'ann_c_only_results.npy', c_only_results, allow_pickle=True)
np.save(DATA_DIR / 'ann_quality_results.npy', quality_results, allow_pickle=True)
np.save(DATA_DIR / 'ann_filter_recalls.npy', filter_recalls, allow_pickle=True)
np.save(DATA_DIR / 'ann_dataset_bits.npy', dataset_bits, allow_pickle=True)
print('\nResults saved for notebooks 74-75.')

ITQ-LSH Accuracy Summary (Recall@10)

Dataset        Dim  Bits    N_train    L=100    L=500   L=1000   L=2000   L=5000   Spearman
------------------------------------------------------------------------------------------
glove          100   100  1,183,514    38.6%    58.5%    66.9%    74.8%    83.9%   -0.5083
sift           128   128  1,000,000    50.0%    76.2%    85.0%    91.6%    96.9%   -0.9252
fashion        784   128     60,000    79.7%    97.2%    99.1%    99.7%    99.9%   -0.7446
nytimes        256   128    290,000    55.2%    68.9%    74.2%    79.4%    85.8%   -0.5084
gist           960   128  1,000,000    26.5%    48.1%    59.4%    70.2%    83.0%   -0.4551

Dataset        Dim    L=100    L=500   L=1000   L=2000   L=5000  (Filter Recall@10)
---------------------------------------------------------------------------
glove          100    38.6%    58.5%    66.9%    74.8%    83.9%
sift           128    50.0%    76.2%    85.0%    91.7%    97.0%
fashion        784    79.7%    97.2

## 評価・考察

### ハッシュ品質（Hamming-Cosine Spearman相関）

ITQ-LSH 128ビットのハッシュ品質はデータセットの特性に大きく依存することが判明した。

| データセット | Spearman | 品質 | 考察 |
|-------------|----------|------|------|
| SIFT | -0.9252 | 非常に良い | 128次元→128ビットで情報損失が最小。PCA空間での構造が単純 |
| Fashion | -0.7446 | 良い | 高次元（784）だがPCA上位128成分に情報が集中 |
| GloVe | -0.5083 | 普通 | 100次元→100ビット（128ビット不可）。次元不足が品質の上限を規定 |
| NYTimes | -0.5084 | 普通 | 256次元あるがテキスト埋め込みの分布がハッシュに不向き |
| GIST | -0.4551 | やや弱い | 960次元→128ビットで大幅な次元圧縮。情報損失が大きい |

**重要な知見**: Spearman相関はデータの「ハッシュ容易性」を反映しており、入力次元とハッシュビット数の比率だけでなく、データの内在的な構造（PCAで圧縮しやすいか）が決定的に重要である。

### C-onlyパイプライン（ITQ → Hamming候補選択 → Cosine rerank）

| データセット | L=100 | L=500 | L=1000 | L=2000 | L=5000 |
|-------------|-------|-------|--------|--------|--------|
| Fashion | 79.7% | 97.2% | 99.1% | 99.7% | 99.9% |
| SIFT | 50.0% | 76.2% | 85.0% | 91.6% | 96.9% |
| NYTimes | 55.2% | 68.9% | 74.2% | 79.4% | 85.8% |
| GloVe | 38.6% | 58.5% | 66.9% | 74.8% | 83.9% |
| GIST | 26.5% | 48.1% | 59.4% | 70.2% | 83.0% |

**候補数とRecallのトレードオフ**:
- **Fashion**: L=500で既に97%を超え、事実上HNSWと同等。小規模データ+高次元でITQ-LSHが最も有効なケース。
- **SIFT**: L=5000で96.9%に到達。候補数を増やせばHNSW（97.9%）に迫れる。
- **GIST/GloVe**: L=5000でも83%台にとどまり、ハッシュ品質の限界がRecallの上限を規定。

### Filter RecallとC-only Recallの関係

Filter Recall（Hamming候補に真のtop-10が含まれる割合）とC-only Recall@10がほぼ一致している。これは、**Cosine rerankステップが候補内の順序を正しく並べ替えており、ボトルネックはHamming候補選択段階にある**ことを意味する。つまり、改善すべきはハッシュ品質（候補選択精度）であり、rerankステップではない。

### ビット数の制約

GloVeは入力次元100に対してITQ-LSHが最大100ビットしか生成できない制約があり、128ビット目標に届かなかった。これは他の128ビットデータセットとの直接比較に注意が必要な点である。ランダム射影等で次元を増やす手法も考えられるが、本実験ではITQのPCA制約に従った。